In [1]:
import numpy as np
import trimesh
import os
import shutil
import imageio.v3 as imageio
from tqdm import tqdm

ModuleNotFoundError: No module named 'trimesh'

In [14]:
import numpy as np

def rotation_matrix(axis, angle):
    """
    Returns a rotation matrix for a given axis and angle in radians.
    :param axis: str, the axis to rotate around ('x', 'y', or 'z')
    :param angle: float, the rotation angle in radians
    :return: 3x3 rotation matrix
    """
    if axis == 'x':
        return np.array([[1, 0, 0],
                         [0, np.cos(angle), -np.sin(angle)],
                         [0, np.sin(angle), np.cos(angle)]])
    elif axis == 'y':
        return np.array([[np.cos(angle), 0, np.sin(angle)],
                         [0, 1, 0],
                         [-np.sin(angle), 0, np.cos(angle)]])
    elif axis == 'z':
        return np.array([[np.cos(angle), -np.sin(angle), 0],
                         [np.sin(angle), np.cos(angle), 0],
                         [0, 0, 1]])
    else:
        raise ValueError("Axis must be 'x', 'y', or 'z'.")

def rotate_point_cloud(point_cloud, rotations):
    """
    Rotates a point cloud along specified axes by the given angles.
    :param point_cloud: Nx3 numpy array of points
    :param rotations: list of tuples [(axis, angle_in_degrees), ...]
                      Example: [('x', 90), ('y', 45)] for composite rotations
    :return: Rotated point cloud as Nx3 numpy array
    """
    rotated_cloud = point_cloud.copy()
    for axis, angle in rotations:
        angle_rad = np.radians(angle)  # Convert degrees to radians
        R = rotation_matrix(axis, angle_rad)
        rotated_cloud = np.dot(rotated_cloud, R.T)  # Apply rotation matrix
    
    return rotated_cloud


In [15]:
# Example point cloud (Nx3 matrix)
point_cloud = np.array([[1, 0, 0],
                        [0, 1, 0],
                        [0, 0, 1]])

# Composite rotation: 90 degrees around x, then 45 degrees around y
rotations = [('x', 90), ('y', 45)]

# Rotate the point cloud
rotated_cloud = rotate_point_cloud(point_cloud, rotations)
print(rotated_cloud)


[[ 7.07106781e-01  0.00000000e+00 -7.07106781e-01]
 [ 7.07106781e-01  6.12323400e-17  7.07106781e-01]
 [ 4.32978028e-17 -1.00000000e+00  4.32978028e-17]]


In [3]:
# rotate different to align in gso canonical space
# import open3d as o3d
# import numpy as np
import plotly.graph_objects as go
import matplotlib.pyplot as plt
import point_cloud_utils as pcu


In [4]:
def vis_colored_pcd(points, colors, size=1.0):

    fig = go.Figure(
      data=[
        go.Scatter3d(
          x=points[:,0], y=points[:,1], z=points[:,2],
          mode='markers',
          marker=dict(size=size, color=colors)
    )

      ],
      layout=dict(    
        paper_bgcolor='rgba(0,0,0,0)', 
        width=512, 
        height=512,
        scene=dict(
          xaxis=dict(visible=False),
          yaxis=dict(visible=False),
          zaxis=dict(visible=False)
    )
    )
    )
    config = {
  'toImageButtonOptions': {
    'format': 'png', # one of png, svg, jpeg, webp
    'filename': 'custom_image',
    'height': 512,
    'width': 512,
    'scale':4 # Multiply title/legend/axis/canvas sizes by this factor
  }
}


    fig.show(config=config)
#     fig.write_image("fig1.png")

# vis_colored_pcd(points, colors, size=1.3)
# vis_colored_pcd(split_points, splint_colors)

In [84]:
from functools import partial
# transformation dictionary
transformation_dict = {
    'gso': partial(rotate_point_cloud, rotations=[('x', 0)]), # no transformation
    'LGM': partial(rotate_point_cloud, rotations=[('x', 90)]),
    'CRM': partial(rotate_point_cloud, rotations=[('x', 90), ('z', 180)]),
    'Lara': partial(rotate_point_cloud, rotations=[('x', -110), ('z', 33)]),
    'ln3diff': partial(rotate_point_cloud, rotations=[('x', 90)]),
    'One-2-3-45': partial(rotate_point_cloud, rotations=[('x', 90), ('z', 180)]),
    'splatter-img': partial(rotate_point_cloud, rotations=[('x', -60)]),
    # 
    'OpenLRM': partial(rotate_point_cloud, rotations=[('x', 0)]),
    'shape-e': partial(rotate_point_cloud, rotations=[('x', 0)]),
    'GA/stage-2/dino_img/ditl-fromditlPCD-fixPose-tomesh-ditxlPCD': partial(rotate_point_cloud, rotations=[('x', 0)]),
}

In [68]:
import os

# instance_name = '3D_Dollhouse_Happy_Brother_pcd_4096'
# instance_name = 'FRUIT_VEGGIE_DOMINO_GRADIENT_pcd_4096'
# instance_name = 'SpiderMan_Titan_Hero_12Inch_Action_Figure_5Hnn4mtkFsP_pcd_4096'
instance_name = 'Android_Figure_Panda_pcd_4096'

method_name='LGM'
save_root=f"/mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir/3D-metrics-fps"

def vis_pcd(method_name, instance_name):

    pcd_path = os.path.join(save_root, method_name, f'{instance_name}.ply')
    pcd = trimesh.load(pcd_path).vertices

    pcd = transformation_dict[method_name](pcd)

    color = np.zeros_like(pcd) # just black
    vis_colored_pcd(pcd, color)

    # return pcd

In [85]:
# vis_pcd('LGM', instance_name)
# vis_pcd('Lara', instance_name) # wrong
# vis_pcd('ln3diff', instance_name) # 
# vis_pcd('CRM', instance_name) # 
# vis_pcd('One-2-3-45', instance_name) # 
# vis_pcd('splatter-img', instance_name) # 
# vis_pcd('shape-e', instance_name) # 
# vis_pcd('CRM', instance_name) # 
# vis_pcd('OpenLRM', instance_name) # 

vis_pcd('GA/stage-2/dino_img/ditl-fromditlPCD-fixPose-tomesh-ditxlPCD', instance_name) # 

In [87]:
vis_pcd('gso', instance_name)
# vis_pcd('shape-e', instance_name) # 
# vis_pcd('LGM', instance_name) # 
# vis_pcd('splatter-img', instance_name) # 

In [5]:
# organize a dataset for fid eval

objv_dataset = '/mnt/sfs-common/yslan/Dataset/Obajverse/chunk-jpeg-normal/bs_16_fixsave3/170K/512/'
dataset_json = os.path.join(objv_dataset, 'dataset.json')

In [6]:
import json
with open(dataset_json, 'r') as f:
    dataset_json = json.load(f)

In [7]:
dataset_json.keys()

dict_keys(['Transportations_tar', 'Furnitures', 'Food', 'BuildingsOutdoor', 'Electronics', 'daily-used', 'Human-Shape', 'Plants', 'Animals'])

In [8]:
len(dataset_json['Animals'])

37461

In [9]:
# instances_for_use = dataset_json['Animals'][::3][:6250]
instances_for_use = dataset_json['Animals'][::3][:6250][1100:2200]
# instances_for_use = dataset_json['Animals'][:6250]

In [10]:
# len(instances_for_use)
instances_for_use[:3]

['Animals/53/275475/1', 'Animals/53/278344/1', 'Animals/53/279428/1']

In [18]:

# save to local dir, with the same format as obj_folder, 8 images 
# output_dir = '/mnt/sfs-common/yslan/Dataset/Obajverse/Objv-animals-for-FID_eval'
output_dir = '/mnt/sfs-common/yslan/Dataset/Obajverse/Objv-animals-for-FID_eval-new'
# output_dir = '/mnt/sfs-common/yslan/Dataset/Obajverse/Objv-animals-for-FID_eval-2K'
# output_dir = '/mnt/sfs-common/yslan/Dataset/Obajverse/Objv-animals-for-FID_eval-2K-new'

# for object in instances_for_use:
for idx, object in enumerate(tqdm(instances_for_use[:])):
    img_path = os.path.join(objv_dataset, object, 'raw_img.jpg')
    img = imageio.imread(img_path)

    if idx % 3 == 0:
        indices_to_save = [0,1]
    else:
        indices_to_save = [1,0]
    # indices_to_save = [0,1,2,3,4,9,10,11,12][:2]
    # else:
        # indices_to_save = [1,2,3,4,9,10,11,12]

    instance_output_dir = os.path.join(output_dir, object)
    os.makedirs(instance_output_dir, exist_ok=True)

    for idx, w_position in enumerate(indices_to_save):
        patch = img[:, w_position*512:(w_position+1)*512, :]
        imageio.imwrite(os.path.join(instance_output_dir, f'{idx}.jpg'), patch)

100%|██████████| 1100/1100 [01:32<00:00, 11.87it/s]


In [12]:
# convert gt pcd to the right format



objv_dataset = '/mnt/sfs-common/yslan/Dataset/Obajverse/chunk-jpeg-normal/bs_16_fixsave3/170K/512/'
dataset_json = os.path.join(objv_dataset, 'dataset.json')
with open(dataset_json, 'r') as f:
    dataset_json = json.load(f)

all_objs = dataset_json['Animals'][::3][1100:2200]

In [18]:
# from tqdm import tqdm        
# import shutil

# ! copy gt

gt_path = "/mnt/sfs-common/yslan/Dataset/Obajverse/FPS_PCD/pcd-V=10_4096_polish_fullset/fps-pcd"
output_path = "/mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-objv/3D-metrics-fps/objv-gt"

for obj_folder in tqdm(all_objs):
    save_name = '-'.join(obj_folder.split('/'))
    obj_folder = '/'.join(obj_folder.split('/')[:-1])

    shutil.copy(os.path.join(gt_path, obj_folder, 'fps-4096.ply'), os.path.join(output_path, f'{save_name}_pcd_4096.ply'))

100%|██████████| 1100/1100 [00:33<00:00, 32.89it/s]


In [23]:
# ! copy ours pred

pred_path = "/mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-objv/GA/stage-2/dino_img/ditl-fromditlPCD"
output_path = "/mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-objv/3D-metrics-fps/GA"

for obj_folder in tqdm(all_objs[:]):
    save_name = '-'.join(obj_folder.split('/'))
    obj_folder = '/'.join(obj_folder.split('/')[1:-1])
    try:
        shutil.copy(os.path.join(pred_path, obj_folder, '0', 'sample-0-gaussian-4096.ply'), os.path.join(output_path, f'{save_name}_pcd_4096.ply'))
    except:
        continue

100%|██████████| 1100/1100 [00:14<00:00, 77.74it/s]


In [17]:
# copy output images into a single folder for clean-FID calculation


objv_dataset = '/mnt/sfs-common/yslan/Dataset/Obajverse/chunk-jpeg-normal/bs_16_fixsave3/170K/512/'
dataset_json = os.path.join(objv_dataset, 'dataset.json')
with open(dataset_json, 'r') as f:
    dataset_json = json.load(f)

# all_objs = dataset_json['Animals'][::3][:6250]
all_objs = dataset_json['Animals'][::3][1100:2200]
all_objs = all_objs[:600]


In [45]:

import shutil

# for method_name in ln3diff-fixpose_192 CRM 
# for method_name in 
# OpenLRM/Animals One-2-3-45/Animals shape-e/Animals splatter-img/Animals 

output_path='/mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-objv'

# for method_name in ['LGM_fixpose', 'GA-fixpose']:
# for method_name in []:
# for method_name in ['LGM_fixpose/Animals', 'GA/stage-2/dino_img/ditl-fromditlPCD/']:
for method_name in ['GA/stage-2/dino_img/ditl-fromditlPCD/']:
# for method_name in ['objv-gt']:
    path = os.path.join(output_path, method_name)
    files = []

    for obj_folder in tqdm(all_objs):
        obj_folder = '/'.join(obj_folder.split('/')[1:])
        for idx in range(24):
            # files.append(os.path.join(path, obj_folder, f'{idx}.jpg'))
            if 'Lara' in path:
                files.append(os.path.join(path, '/'.join(obj_folder.split('/')[:-1]), '0.jpg', f'{idx}.jpg'))
            # elif 'LGM' in path:
            #     files.append(os.path.join(path, '/'.join(obj_folder.split('/')[:-1]), '0', f'{idx}.jpg'))
            elif 'GA' in path:
                files.append(os.path.join(path, '/'.join(obj_folder.split('/')[:-1]), '0', f'sample-0-{idx}.jpg'))
            elif 'LRM' in path:
                files.append(os.path.join(path, '/'.join(obj_folder.split('/')[:-1]), '0', f'{idx}.jpg'))
            else:
                files.append(os.path.join(path, obj_folder, '0', f'{idx}.jpg'))



    output_path = '/mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-objv/lint-dir'

    method_output_path = os.path.join(output_path, method_name)
    os.makedirs(method_output_path, exist_ok=True)

    for idx, file_path in enumerate(tqdm(files[:])):
        shutil.copy(file_path, os.path.join(method_output_path, f'{idx}.jpg'))


100%|██████████| 14400/14400 [03:20<00:00, 71.66it/s]


100%|██████████| 10/10 [00:00<00:00, 60.38it/s]


In [40]:
os.path.join(method_output_path, f'{idx}.jpg')

'/mnt/sfs-common/yslan/Dataset/Obajverse/Objv-animals-for-FID_eval-new/LGM_fixpose/Animals/9.jpg'

In [18]:
gso_rendering="/mnt/sfs-common/yslan/Dataset/Obajverse/Objv-animals-for-FID_eval-2K"


# for method_name in ['GA/stage-2/dino_img/ditl-fromditlPCD/']:
# # for method_name in ['objv-gt']:
#     path = os.path.join(output_path, method_name)
files = []

for obj_folder in tqdm(all_objs):
    obj_folder = obj_folder[:-2] # to load 3 chunks
    for batch in range(1,4):
        for idx in range(8):
            files.append(os.path.join(gso_rendering, obj_folder, str(batch), f'{idx}.jpg'))


100%|██████████| 600/600 [00:00<00:00, 20171.71it/s]


In [23]:

output_path = '/mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-objv/lint-dir'
gt_output_path = os.path.join(output_path, 'objv-gt')

os.makedirs(gt_output_path, exist_ok=True)

for idx, file_path in enumerate(tqdm(files[:])):
    shutil.copy(file_path, os.path.join(gt_output_path, f'{idx}.jpg'))

100%|██████████| 14400/14400 [04:21<00:00, 55.06it/s]


In [5]:
all_vid_paths = "/mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-free3d/GA-fixpose/2-30_CONSTRUCTION_SET-0-sample-0-gs.mp4 /mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-free3d/GA-fixpose/60-BAGEL_WITH_CHEESE-0-sample-0-gs.mp4 /mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-free3d/GA-fixpose/62-BALANCING_CACTUS-0-sample-0-gs.mp4 /mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-free3d/GA-fixpose/76-Baby_Elements_Stacking_Cups-0-sample-0-gs.mp4 /mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-free3d/GA-fixpose/98-Breyer_Horse_Of_The_Year_2015-0-sample-0-gs.mp4 /mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-free3d/GA-fixpose/112-COAST_GUARD_BOAT-0-sample-0-gs.mp4 /mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-free3d/GA-fixpose/113-CONE_SORTING-0-sample-0-gs.mp4 /mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-free3d/GA-fixpose/115-CREATIVE_BLOCKS_35_MM-0-sample-0-gs.mp4 /mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-free3d/GA-fixpose/155-Cole_Hardware_Mini_Honey_Dipper-0-sample-0-gs.mp4 /mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-free3d/GA-fixpose/275-FAIRY_TALE_BLOCKS-0-sample-0-gs.mp4 /mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-free3d/GA-fixpose/277-FIRE_ENGINE-0-sample-0-gs.mp4 /mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-free3d/GA-fixpose/280-FOOD_BEVERAGE_SET-0-sample-0-gs.mp4 /mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-free3d/GA-fixpose/303-GEOMETRIC_PEG_BOARD-0-sample-0-gs.mp4 /mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-free3d/GA-fixpose/324-Great_Dinos_Triceratops_Toy-0-sample-0-gs.mp4 /mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-free3d/GA-fixpose/365-JUICER_SET-0-sample-0-gs.mp4 /mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-free3d/GA-fixpose/789-STACKING_BEAR-0-sample-0-gs.mp4 /mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-free3d/GA-fixpose/791-STACKING_RING-0-sample-0-gs.mp4 /mnt/sfs-common/yslan/Repo/3dgen/FID-KID-Outputdir-free3d/GA-fixpose/803-Schleich_African_Black_Rhino-0-sample-0-gs.mp4 "

In [9]:
instances = [
    path.split('/')[-1].split('-')[1]
    for path in all_vid_paths.split()
]
instances[1:]

['BAGEL_WITH_CHEESE',
 'BALANCING_CACTUS',
 'Baby_Elements_Stacking_Cups',
 'Breyer_Horse_Of_The_Year_2015',
 'COAST_GUARD_BOAT',
 'CONE_SORTING',
 'CREATIVE_BLOCKS_35_MM',
 'Cole_Hardware_Mini_Honey_Dipper',
 'FAIRY_TALE_BLOCKS',
 'FIRE_ENGINE',
 'FOOD_BEVERAGE_SET',
 'GEOMETRIC_PEG_BOARD',
 'Great_Dinos_Triceratops_Toy',
 'JUICER_SET',
 'STACKING_BEAR',
 'STACKING_RING',
 'Schleich_African_Black_Rhino']